In [1]:
# Standard Libraries
import os

# External Libraries
import click
import pandas as pd
import altair as alt
from sklearn import datasets
from sklearn.model_selection import train_test_split
from sklearn.ensemble import RandomForestClassifier
from sklearn.metrics import confusion_matrix
import mlflow.sklearn
from mlflow.models.signature import infer_signature
import altair as alt
import altair_viewer

# Internal Libraries
import mlflow_vismod


# Remove Max Rows Limit in Altair
alt.data_transformers.disable_max_rows()

DataTransformerRegistry.enable('default')

In [2]:
# MLflow
MLFLOW_TRACKING_URI = 'http://localhost:5000'
EXPERIMENT = 'iris'

# Sklearn Model
TEST_SIZE = 0.33
RANDOM_STATE = 42

/Users/jhibba/miniconda3/envs/mlflow-vizmod/lib/python3.8/site-packages/ipykernel/ipkernel.py:287: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


In [3]:
os.environ['MLFLOW_TRACKING_URI'] = MLFLOW_TRACKING_URI
mlflow.set_experiment(EXPERIMENT)

INFO: 'iris' does not exist. Creating a new experiment


In [4]:
# Preprocess Example Iris Dataset
iris = datasets.load_iris(as_frame=True, )
X_train, X_test, y_train, y_test = train_test_split(
    iris['data'],
    iris['target'],
    test_size=TEST_SIZE,
    random_state=RANDOM_STATE,
)

# Preprocessing Example 
diamonds = pd.read_csv('diamonds.csv')
X_dtrain, X_dtest, y_dtrain, y_dtest = train_test_split(
    diamonds[['carat', 'cut', 'color', 'clarity', 'depth', 'table', 'x', 'y', 'z', ]],
    diamonds[['price', ]],
    test_size=TEST_SIZE,
    random_state=RANDOM_STATE,
)

# Viz Model Flavor
#### Use Cases and API

- The concept of a model extends far beyond machine learning encompassing any approximation of a system or process we wish to understand
- Machine learning models fit into a category of mathematically rigorous models that can be developed and used with the scientific method (hypothesis testing etc.) but are by no means the beginning or end of the model space continuum
- Visualizations can be used as models themselves or a means of visually communicating the results, quality etc. of machine learning or other models, to reduce cognitive load on the end user.  
- Visualizations require code/concept development and design like any other model this process needs to be captured to be re-usable and reproduceable
- Re-usability and deployability can be enhanced by including the visualization code in a registry, ready to accept compliant data to visualize, much like a machine learning model can be serialized, and deployed, ready to accept new instances of data for inference
- This pattern could very effective at orchestrating de-centralized data science workflows, typically found in Academia, healthcare, and small startups.  It allows developers to push and pull visualizations from a central registry (ie. MLflow deployed with Databricks or as part of a service stack on cloud VMs).

## General Viz Model Flavor API

The Viz Model flavor API follows the general MLflow API, conceptually.  The flavor is the top level API for visualization models, which can accept user submitted styles, for extension and customization of display and other functionalty specific to the base visualization libary and/or use case.

In [5]:
# Example MLflow Model Run:
# - sklearn flavor
with mlflow.start_run() as run:
    # Define and Fit Model
    clf = RandomForestClassifier(max_depth=7, random_state=RANDOM_STATE)
    clf.fit(X_train, y_train)
    
    # Log Accuracy
    mlflow.log_metric('accuracy', value=clf.score(X_test, y_test))
    
    # Log Model
    mlflow.sklearn.log_model(
        sk_model=clf,
        artifact_path='model',
        signature=infer_signature(X_train, clf.predict(X_train)),
    )

#### Log visualization model and artifacts:
- seralize visualization code
- log artifacts at an artifact path (typically relevant json, html)

In [6]:
# Example MLflow Model Run
# - vizmod flavor
# - vegalite `style`
with mlflow.start_run() as run1:
    # Define Viz
    viz1 = alt.Chart(
        pd.concat([X_train, y_train], axis=1, sort=False)
    ).mark_circle(size=60).encode(
        x='sepal length (cm)',
        y='sepal width (cm)',
        color='target:N'
    ).properties(
        height=375,
        width=575,
    ).interactive()
    
    # Log Model
    mlflow_vismod.log_model(
        model=viz1, 
        artifact_path='viz',
        style='vegalite',
        signature=infer_signature(X_train, None),
        input_example=pd.concat([X_train, y_train], axis=1, sort=False),
    )
    
    # Optional: log artifact
    viz1.save('./example.html')
    mlflow.log_artifact(local_path='./example.html', artifact_path='charts')


# Example MLflow Model Run
# - vizmod flavor
# - vegalite `style`
# - different data
with mlflow.start_run() as run:
    # Define Viz
    viz2 = alt.Chart(
        pd.concat([X_dtrain, y_dtrain], axis=1, sort=False)
    ).mark_circle(size=60).encode(
        x='carat',
        y='clarity',
        color='cut:N'
    ).properties(
        height=375,
        width=575,
    ).interactive()
    
    # Log Model
    mlflow_vismod.log_model(
        model=viz2, 
        artifact_path='viz',
        style='vegalite',
        signature=infer_signature(X_train, None),
        input_example=pd.concat([X_train, y_train], axis=1, sort=False),
    )
    
    # Optional: log artifact
    viz2.save('./example.html')
    mlflow.log_artifact(local_path='./example.html', artifact_path='charts')


viz1 | viz2

/Users/jhibba/miniconda3/envs/mlflow-vizmod/lib/python3.8/site-packages/ipykernel/ipkernel.py:287: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


alt.HConcatChart(...)

#### Register visualization model and artifacts:

Send logged visualizations to the MLflow registry for use in dev, orchestration, and deployment

#### Update vizualization data object:

Just like an ML model must be able to accept new instances of data for inference and that instance must be compliant with the model in terms of features, so must a visualization be able to accept and render new instances of compliant data

In [7]:
model_uri = os.path.join(run1.to_dictionary()['info']['artifact_uri'], 'viz')
loaded = mlflow_vismod.load_model(
    model_uri=model_uri,
    style='vegalite'
)

# Rendering new data / subset of data
new_data = pd.concat([X_train, y_train], axis=1, sort=False)
loaded.display(model_input=new_data[new_data['target'] != 2])

alt.Chart(...)

## Typical Model Styles:

- **ggplot:** an R library based on the grammar of graphics, which is particularly effective for leveraging R dataframes.
- **Altair:** is a declarative python library which serves as an API to vegalite, an declarative JS based visualization libary based on the grammer of graphics. This library is useful for simple to complex visualizations leveraging pandas, for display in python environments or export to HTML for display on the web
- **matplotlib/seaborn:** popular python viz libraries

## Example Use Cases 
 
 - Visualize Performance Metrics and Register With ML Model:
     + create a scatter plot predicted vs ground truth and color by correctness
     + use the diplay function to wrap an example in html
     + register the visualization and html artifact along with the model
     + another developer or user can see the diagnostic in the registry and pull down the model plus visualization for re-use and extension

In [8]:
predictions_viz = alt.Chart(
    pd.concat([X_test, y_test, clf.predict(X_test) == y_test], axis=1, sort=False)
).mark_circle(size=60).encode(
    x='sepal length (cm)',
    y='sepal width (cm)',
    color='target:N'
).properties(
    height=375,
    width=575,
).interactive()

predictions_viz

/Users/jhibba/miniconda3/envs/mlflow-vizmod/lib/python3.8/site-packages/ipykernel/ipkernel.py:287: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)
/Users/jhibba/miniconda3/envs/mlflow-vizmod/lib/python3.8/site-packages/altair/utils/data.py:150: UserWarning: DataFrame columns are not unique, some columns will be omitted.
  return {"values": data.to_dict(orient="records")}


alt.Chart(...)

- Visualize a key message of a model for end user consumption:
    + Pull a generalized model from a registry (ie. a scatter plot that accepts x, y, and color by variable)
    + Point the model at a compliant instance of data or entire data set to visualize
    + deploy rendered model to the end user
    
    Note for scenarios like, the data set could be dynamic (new data points coming in) and the code associated with the visualization could be an entire transformation pipeline, jsut as sklearn or other models can be associated with data transformations as part of sklearn pipeline objects.  This is particularly effective with altair models, which can include Pandas and related pipelines, out of the box
​

- Deploy an interactive web visualization: This use case is particuarly effective with Vegalite, since models are encoded as JSON objects, which accept pointers to data.  This means you can store the JSON object as an artifact and use the visualization API to point it at new data.
    + Encode a visualization (ie. a geo map for ICU bed utilization and covid cases for each county in the USA with size/color encodings and tooltips which help the end user make decisions on where patients or resources should be sent)
    + register the visualization
    + pull the visualization and point it at a compliant data set of interest
    + deploy to a website (the website would already have panel or some other mechanism of accpeting the registered visualization)
    + alter the visualization as needed, using registry tags to point the new version of the model

In [9]:
import altair_viewer


altair_viewer.display(loaded.model)

/Users/jhibba/miniconda3/envs/mlflow-vizmod/lib/python3.8/site-packages/ipykernel/ipkernel.py:287: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


Displaying chart at http://localhost:20911/